In [7]:
# Function to load data from an ARFF file
def load_arff(file_path):
    # Read all lines from the file
    with open(file_path, 'r') as f:
        lines = f.readlines()

    # Find the start of the data section
    data_start = lines.index('@data\n') + 1

    # Extract attribute names from the file
    attributes = [line.split()[1] for line in lines if line.startswith('@attribute')]

    # Create a list to store dictionaries representing each data entry
    data_list = []

    # Parse data values and create dictionaries
    for line in lines[data_start:]:
        values = line.strip().split(',')
        # Use a dictionary comprehension to handle missing values ('m' in this case)
        data_dict = {attr: val if val != 'm' else None for attr, val in zip(attributes, values)}
        data_list.append(data_dict)

    return data_list

# Function to preprocess data by replacing 'm' with None
def preprocess_data(data_list):
    for entry in data_list:
        for key, value in entry.items():
            if value == 'm':
                entry[key] = None

    return data_list

# Function to perform linear interpolation on data
def linear_interpolation(data_list):
    for i in range(1, len(data_list) - 1):
        for key, value in data_list[i].items():
            if value is None and data_list[i - 1][key] is not None and data_list[i + 1][key] is not None:
                # Perform linear interpolation
                data_list[i][key] = (float(data_list[i - 1][key]) + float(data_list[i + 1][key])) / 2

    return data_list

# Function for Z-score standardization on a matrix
def z_score_standardization(matrix):
    for i in range(2, len(matrix[0])):
        column = [float(row[i]) for row in matrix if row[i] is not None and row[i] != 'm']

        # Skip standardization if all values are the same
        if len(set(column)) == 1:
            continue

        mean_val = sum(column) / len(column)

        if len(column) > 1:
            std_dev = (sum((x - mean_val) ** 2 for x in column) / len(column)) ** 0.5
        else:
            std_dev = 0

        # Standardize the column
        for row in matrix:
            if row[i] is not None and row[i] != 'm':
                if std_dev != 0:
                    row[i] = (float(row[i]) - mean_val) / std_dev
                else:
                    row[i] = 0

    return matrix

# Function for dot product of two vectors
def dot_product(v1, v2):
    # Use a generator expression to calculate dot product for numeric values
    result = sum(x * y for x, y in zip(v1, v2) if isinstance(x, (int, float)) and isinstance(y, (int, float)))
    return result

# Function to subtract one vector from another
def subtract(v1, v2):
    return [x - y for x, y in zip(v1, v2)]

# Function to scale a vector by a scalar
def scale(vector, scalar):
    return [x * scalar for x in vector]

# Function to multiply a matrix by a vector
def multiply_matrix_vector(matrix, vector):
    return [dot_product(row, vector) for row in matrix]

# Function to multiply two matrices
def multiply_matrix(matrix1, matrix2):
    result = []
    for row in matrix1:
        new_row = []
        # Use a transpose function to get the columns of matrix2
        for col in transpose(matrix2):
            element = dot_product(row, col)
            new_row.append(element)
        result.append(new_row)
    return result

# Function to transpose a matrix
def transpose(matrix):
    return [[row[i] for row in matrix] for i in range(len(matrix[0]))]

# Function to calculate mean of a column
def mean(column):
    values = [float(val) for val in column if val is not None]
    return sum(values) / len(values) if values else 0

# Function to calculate covariance matrix
def covariance_matrix(matrix):
    n = len(matrix)
    num_features = len(matrix[0])
    transposed_matrix = transpose(matrix)
    cov_matrix = [[0] * num_features for _ in range(num_features)]

    # Calculate covariance matrix
    for i in range(num_features):
        for j in range(num_features):
            mean_i = mean(matrix[i])
            mean_j = mean(matrix[j])
            values_i = [float(val) for val in matrix[i] if val is not None]
            values_j = [float(val) for val in matrix[j] if val is not None]
            cov_matrix[i][j] = sum((val_i - mean_i) * (val_j - mean_j) for val_i, val_j in zip(values_i, values_j)) / (n - 1)

    return cov_matrix

# Custom random number generator function
def custom_random():
    seed = 1
    while True:
        seed = (seed * 1103515245 + 12345) & 0x7FFFFFFF
        yield seed / 0x7FFFFFFF

# Function for Principal Component Analysis (PCA)
def pca(data_matrix, num_components):
    cov_matrix = covariance_matrix(data_matrix)

    num_features = len(data_matrix[0])
    eigenvalues = [0] * num_features
    eigenvectors = [[0] * num_features for _ in range(num_features)]

    random_generator = custom_random()

    # Calculate eigenvalues and eigenvectors
    for i in range(num_features):
        vector = [next(random_generator) for _ in range(num_features)]

        for _ in range(1000):
            new_vector = multiply_matrix_vector(cov_matrix, vector)
            magnitude = sum(x ** 2 for x in new_vector) ** 0.5
            vector = scale(new_vector, 1 / magnitude)

        eigenvalues[i] = dot_product(new_vector, vector)
        eigenvectors[i] = vector

    # Sort indices based on eigenvalues
    sorted_indices = sorted(range(num_features), key=lambda k: eigenvalues[k], reverse=True)
    eigenvalues = [eigenvalues[i] for i in sorted_indices]
    eigenvectors = [[eigenvectors[j][i] for j in sorted_indices] for i in range(num_features)]

    # Select top eigenvectors
    top_eigenvectors = eigenvectors[:num_components]

    # Perform PCA and obtain result matrix
    pca_result = multiply_matrix(data_matrix, transpose(top_eigenvectors))

    return pca_result

# Function to display data table
def display_data_table(data_list):
    attributes = list(data_list[0].keys())

    # Calculate column widths for neat display
    column_widths = {attr: max(len(attr), max(len(str(entry[attr])) for entry in data_list)) for attr in attributes}

    # Display header
    header = "|".join(f"{attr:^{column_widths[attr]}}" for attr in attributes)
    print(header)
    print("-" * sum(column_widths.values()))

    # Display rows
    for entry in data_list:
        row = "|".join(f"{str(entry[attr]):^{column_widths[attr]}}" if entry[attr] is not None else 'm' for attr in attributes)
        print(row)

# Function to display matrix
def display_matrix(matrix):
    for row in matrix:
        formatted_row = "|".join(f"{float(cell):^14.4f}" if cell is not None and cell != 'm' else 'm' for cell in row)
        print(formatted_row)

# Paths to ARFF files
file_path_2017 = r'.\V4 data\2017.arff' 
file_path_2018 = r'.\V4 data\2018.arff'
file_path_2019 = r'.\V4 data\2019.arff'
file_path_2020 = r'.\V4 data\2020.arff'
file_path_2021 = r'.\V4 data\2021 Q1.arff'

# Load data from ARFF files
data_2017 = load_arff(file_path_2017)
data_2018 = load_arff(file_path_2018)
data_2019 = load_arff(file_path_2019)
data_2020 = load_arff(file_path_2020)
data_2021 = load_arff(file_path_2021)

# Preprocess data
data_2017_preprocessed = preprocess_data(data_2017)
data_2018_preprocessed = preprocess_data(data_2018)
data_2019_preprocessed = preprocess_data(data_2019)
data_2020_preprocessed = preprocess_data(data_2020)
data_2021_preprocessed = preprocess_data(data_2021)

# Perform linear interpolation on preprocessed data
data_2017_preprocessed = linear_interpolation(data_2017_preprocessed)
data_2018_preprocessed = linear_interpolation(data_2018_preprocessed)
data_2019_preprocessed = linear_interpolation(data_2019_preprocessed)
data_2020_preprocessed = linear_interpolation(data_2020_preprocessed)
data_2021_preprocessed = linear_interpolation(data_2021_preprocessed)

# Combine data from different years
data_combined = data_2017_preprocessed + data_2018_preprocessed + data_2019_preprocessed + data_2020_preprocessed + data_2021_preprocessed

# Display the type of the combined data
print(type(data_combined))

# Extract attributes from the combined data
attributes = list(data_combined[0].keys())

# Create a matrix from the combined data
matrix = []

for entry in data_combined:
    row = [entry[attr] for attr in attributes[2:]]
    matrix.append(row)

# Perform Z-score standardization on the matrix
standardized_data = z_score_standardization(matrix)

# Display the standardized data matrix
display_matrix(standardized_data)

# Set the number of components for PCA
num_components = 2 

# Perform PCA on the standardized data
pca_result = pca(standardized_data, num_components)

# Display the PCA result
print("\n\nPCA Result:")
display_matrix(pca_result)

    0.1400    |    0.5300    |    0.0033    |   -0.0625    |   -0.0209    |    0.0227    |   -0.0694    |   -0.0215    |   -0.0215    |    0.0227    |    0.0221    |    0.0212    |    0.0709    |    0.0217    |   -0.0673    |    0.0224    |    0.0234    |    0.0227    |    0.0088    |   -0.0215    |    0.0085    |   -0.0280    |    0.0105    |    1.3848    |   -0.0309    |   -0.0339    |   -0.0248    |   -0.0220    |   -0.5009    |   -0.0215    |   -0.0799    |   -0.0215    |   -0.8151    |   -0.0132    |    0.0275    |    0.0510    |   -0.0453    |   -0.0212    |    0.0242    |   -0.0508    |   -0.0227    |    0.0119    |    0.0110    |    2.1530    |   -0.0278    |   -0.0781    |    0.1673    |    0.3745    |   -0.0613    |   -0.0588    |    0.0242    |m|m|   -0.0209    |    0.0006    |    0.0208    |   -0.0099    |    0.0207    |m|   -0.0403    |   -0.0412    |m|m|m|m|   -0.0290    |   -0.0448    |   -0.0538    |   -0.0354    |   -0.0215    |   -0.1269    |   -0.0249    |   -0.0178 

NameError: name 'qr_algorithm' is not defined

In [ ]:
import numpy as np
from sklearn.decomposition import PCA
from sklearn.decomposition import TruncatedSVD
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer

def load_arff(file_path):
    with open(file_path, 'r') as f:
        lines = f.readlines()
    data_start = lines.index('@data\n') + 1
    attributes = [line.split()[1] for line in lines if line.startswith('@attribute')]
    data_list = []
    for line in lines[data_start:]:
        values = line.strip().split(',')
        data_dict = {attr: val if val != 'm' else None for attr, val in zip(attributes, values)}
        data_list.append(data_dict)

    return data_list


def preprocess_data(data_list):
    for entry in data_list:
        for key, value in entry.items():
            if value == 'm':
                entry[key] = None

    return data_list

def linear_interpolation(data_list):
    for i in range(1, len(data_list) - 1):
        for key, value in data_list[i].items():
            if value is None and data_list[i - 1][key] is not None and data_list[i + 1][key] is not None:
                data_list[i][key] = (float(data_list[i - 1][key]) + float(data_list[i + 1][key])) / 2

    return data_list

def z_score_standardization(matrix):
    for i in range(2, len(matrix[0])):
        column = [float(row[i]) for row in matrix if row[i] is not None and row[i] != 'm']
        if len(set(column)) == 1:
            continue

        mean_val = sum(column) / len(column)

        if len(column) > 1:
            std_dev = (sum((x - mean_val) ** 2 for x in column) / len(column)) ** 0.5
        else:
            std_dev = 0

        for row in matrix:
            if row[i] is not None and row[i] != 'm':
                if std_dev != 0:
                    row[i] = (float(row[i]) - mean_val) / std_dev
                else:
                    row[i] = 0 

    return matrix


def custom_random():
    seed = 1
    while True:
        seed = (seed * 1103515245 + 12345) & 0x7FFFFFFF
        yield seed / 0x7FFFFFFF


def svd_sklearn(data_matrix, num_components):
    imputer = SimpleImputer(strategy='mean')
    data_matrix_imputed = imputer.fit_transform(data_matrix)

    scaler = StandardScaler()
    data_matrix_standardized = scaler.fit_transform(data_matrix_imputed)

    svd = TruncatedSVD(n_components=num_components)
    svd_result = svd.fit_transform(data_matrix_standardized)

    return svd_result


def pca_sklearn_with_imputation(data_matrix, num_components):
    imputer = SimpleImputer(strategy='mean')
    data_matrix_imputed = imputer.fit_transform(data_matrix)

    scaler = StandardScaler()
    data_matrix_standardized = scaler.fit_transform(data_matrix_imputed)

    pca = PCA(n_components=num_components)
    pca_result = pca.fit_transform(data_matrix_standardized)

    return pca_result


def display_matrix(matrix):
    for row in matrix:
        print("|".join(f"{str(cell):^10}" for cell in row))

file_path_2017 = r'.\V4 data\2017.arff' 
file_path_2018 = r'.\V4 data\2018.arff'
file_path_2019 = r'.\V4 data\2019.arff'
file_path_2020 = r'.\V4 data\2020.arff'
file_path_2021 = r'.\V4 data\2021 Q1.arff'

data_2017 = load_arff(file_path_2017)
data_2018 = load_arff(file_path_2018)
data_2019 = load_arff(file_path_2019)
data_2020 = load_arff(file_path_2020)
data_2021 = load_arff(file_path_2021)

data_2017_preprocessed = preprocess_data(data_2017)
data_2018_preprocessed = preprocess_data(data_2018)
data_2019_preprocessed = preprocess_data(data_2019)
data_2020_preprocessed = preprocess_data(data_2020)
data_2021_preprocessed = preprocess_data(data_2021)

data_2017_preprocessed = linear_interpolation(data_2017_preprocessed)
data_2018_preprocessed = linear_interpolation(data_2018_preprocessed)
data_2019_preprocessed = linear_interpolation(data_2019_preprocessed)
data_2020_preprocessed = linear_interpolation(data_2020_preprocessed)
data_2021_preprocessed = linear_interpolation(data_2021_preprocessed)


data_combined = data_2017_preprocessed + data_2018_preprocessed + data_2019_preprocessed + data_2020_preprocessed + data_2021_preprocessed
display_data_table(data_combined)


attributes = list(data_combined[0].keys())


matrix = []
for entry in data_combined:
    row = [entry[attr] for attr in attributes[2:]] 
    matrix.append(row)


standardized_data = z_score_standardization(matrix)

num_components = 2
pca_result_sklearn = pca_sklearn_with_imputation(standardized_data, num_components)


print("\nScikit-learn PCA Result:")
display_matrix(pca_result_sklearn)

svd_result_sklearn = svd_sklearn(standardized_data, num_components)

print("\nScikit-learn SVD Result:")
display_matrix(svd_result_sklearn)

Num|    Country     |         X1          |        X2         |         X3          |        X4        |         X5          |         X6          |         X7          |        X8         |         X9          |         X10          |         X11          |         X12          |         X13         |         X14         |       X15        |         X16          |         X17          |         X18          |         X19          |        X20        |         X21          |        X22        |         X23         |       X24        |         X25         |         X26         |        X27        |        X28        |        X29         |        X30        |        X31        |         X32         |       X33        |        X34         |         X35         |         X36          |        X37        |         X38         |         X39          |        X40        |        X41        |        X42         |        X43        |       X44        |         X45         |         X46         

In my custom implementation and scikit-learn library, both Principal Component Analysis (PCA) and Singular Value Decomposition (SVD) are performed on the dataset. While similarities exist, differences in handling missing values, linear interpolation, standardization, random initialization, the number of iterations, and zero variance may contribute to variations in results. In my code, I replace missing values with None, whereas scikit-learn uses SimpleImputer to replace them with means during SVD and PCA. The interpolation and standardization procedures need to align closely between the two implementations. Additionally, the random initialization of eigenvectors, the number of iterations in power iteration, and the treatment of zero variance can impact the outcome. To investigate discrepancies, a careful comparison of intermediate results at each step, such as mean, covariance matrix, eigenvectors, and eigenvalues, is essential. Running both implementations with the same random seed can enhance reproducibility for a more accurate comparison.